In [2]:
#Imports
import pandas as pd
import numpy as np
from typing import Dict, List
from collections import OrderedDict
import datetime as datetime
from pandas.tseries.offsets import *
from IPython.core.debugger import set_trace
#import pixiedust
#ctrl-shift-p for the command palette
pd.set_option("max_colwidth", 100)
pd.set_option("display.max_rows", 100000)
pd.set_option("display.max_columns", 1000)

In [3]:
options_data = '../data/Options/vix_w_futures.csv'

options = pd.read_csv(
    options_data,
    header=0,
    parse_dates=["quote_date", "expiration"],
)
options.head()

underlying_symbol quote_date root expiration  strike option_type  open  \
0              ^VIX 2006-02-27  VIX 2006-04-19    10.0           c  2.80   
1              ^VIX 2006-02-27  VIX 2006-04-19    10.0           p  0.00   
2              ^VIX 2006-02-27  VIX 2006-04-19    12.5           c  1.15   
3              ^VIX 2006-02-27  VIX 2006-04-19    12.5           p  0.00   
4              ^VIX 2006-02-27  VIX 2006-04-19    12.5           c  0.00   

   high  low  close  trade_volume  bid_size_1545  bid_1545  ask_size_1545  \
0  2.80  2.8    2.8          10.0            1.0      2.70           50.0   
1  0.00  0.0    0.0           0.0            0.0      0.00           50.0   
2  1.15  1.1    1.1          30.0           10.0      1.15           50.0   
3  0.00  0.0    0.0           0.0           50.0      0.75            1.0   
4  0.00  0.0    0.0           0.0            0.0      0.00            0.0   

   ask_1545  underlying_bid_1545  underlying_ask_1545  bid_size_eod  \
0      2.90                11.47                11.47           1.0   
1      0.15                11.47                11.47           0.0   
2      1.20                11.47                11.47          10.0   
3      0.90                11.47                11.47          10.0   
4      0.00                11.47                11.47           0.0   

   ask_size_eod  vwap  open_interest  delivery_code  futures  mid_eod  \
0          10.0  2.80           23.0              0     12.5    2.950   
1          50.0  0.00            0.0              0     12.5    0.075   
2          10.0  1.13          560.0              0     12.5    1.300   
3          10.0  0.00          975.0              0     12.5    0.875   
4           0.0  0.00            0.0              0     12.5    0.000   

   mid_underlying  
0           11.59  
1           11.59  
2           11.59  
3           11.59  
4           11.59

In [4]:
expiry_dates=options.expiration.unique()

In [5]:
puts_data = '../data/Options/vixPuts.csv'
#puts_data='../data/Options/vxxPuts.csv'
puts = pd.read_csv(
    puts_data,
    header=0,
    parse_dates=["quote_date", "expiration"],
    usecols=[
        "quote_date", "expiration", "strike", 'trade_volume',"mid_eod", "mid_underlying","futures"
    ])
puts.head()

quote_date expiration  strike  trade_volume  futures  mid_eod  \
0 2006-02-27 2006-04-19    10.0           0.0     12.5    0.075   
1 2006-02-27 2006-04-19    12.5           0.0     12.5    0.875   
2 2006-02-27 2006-04-19    12.5           0.0     12.5    0.000   
3 2006-02-27 2006-04-19    15.0           0.0     12.5    2.700   
4 2006-02-27 2006-04-19    15.0           0.0     12.5    0.000   

   mid_underlying  
0           11.59  
1           11.59  
2           11.59  
3           11.59  
4           11.59

In [6]:
len(puts.expiration.unique())

154

In [7]:
#insert some column markers so we know when days, months change

first_filter=puts.quote_date.isin(expiry_dates)
second_filter=puts.quote_date.isin(expiry_dates).shift(1)

puts['DSame'] = puts.quote_date.eq(puts.quote_date.shift(-1))
#puts['MSame'] = puts.quote_date.dt.month.eq(
#    puts.quote_date.dt.month.shift(1))
puts['MSame']=(first_filter==True) & (second_filter==False)

puts.head()

quote_date expiration  strike  trade_volume  futures  mid_eod  \
0 2006-02-27 2006-04-19    10.0           0.0     12.5    0.075   
1 2006-02-27 2006-04-19    12.5           0.0     12.5    0.875   
2 2006-02-27 2006-04-19    12.5           0.0     12.5    0.000   
3 2006-02-27 2006-04-19    15.0           0.0     12.5    2.700   
4 2006-02-27 2006-04-19    15.0           0.0     12.5    0.000   

   mid_underlying  DSame  MSame  
0           11.59   True  False  
1           11.59   True  False  
2           11.59   True  False  
3           11.59   True  False  
4           11.59   True  False

In [8]:
calls_data = '../data/Options/vixCalls.csv'
#calls_data='../data/Options/vxxCalls.csv'

calls = pd.read_csv(
    calls_data,
    header=0,
    parse_dates=["quote_date", "expiration"],
    usecols=[
        "quote_date", "expiration", "strike", 'trade_volume', "mid_eod",
        "mid_underlying","futures"
    ])
calls.head()

quote_date expiration  strike  trade_volume  futures  mid_eod  \
0 2006-02-27 2006-04-19    10.0          10.0     12.5     2.95   
1 2006-02-27 2006-04-19    12.5          30.0     12.5     1.30   
2 2006-02-27 2006-04-19    12.5           0.0     12.5     0.00   
3 2006-02-27 2006-04-19    15.0        3001.0     12.5     0.65   
4 2006-02-27 2006-04-19    15.0           0.0     12.5     0.00   

   mid_underlying  
0           11.59  
1           11.59  
2           11.59  
3           11.59  
4           11.59

In [9]:
len(calls.expiration.unique())

154

In [10]:
#insert some column markers so we know when days, months change
first_filter=calls.quote_date.isin(expiry_dates)
second_filter=calls.quote_date.isin(expiry_dates).shift(1)
calls['DSame'] = calls.quote_date.eq(calls.quote_date.shift(-1))
#calls['MSame'] = calls.quote_date.dt.month.eq(
    #calls.quote_date.dt.month.shift(1))
calls['MSame'] =(first_filter==True) & (second_filter==False)
calls.head()

quote_date expiration  strike  trade_volume  futures  mid_eod  \
0 2006-02-27 2006-04-19    10.0          10.0     12.5     2.95   
1 2006-02-27 2006-04-19    12.5          30.0     12.5     1.30   
2 2006-02-27 2006-04-19    12.5           0.0     12.5     0.00   
3 2006-02-27 2006-04-19    15.0        3001.0     12.5     0.65   
4 2006-02-27 2006-04-19    15.0           0.0     12.5     0.00   

   mid_underlying  DSame  MSame  
0           11.59   True  False  
1           11.59   True  False  
2           11.59   True  False  
3           11.59   True  False  
4           11.59   True  False

In [11]:
#initialise variables
#what length of option are you looking for in days?
put_Expiration = int(200)
#<1=OTM, 1=ATM, >1=ITM
put_moneyness=1.00

In [12]:
#%%pixie_debugger
#initialise variables

temp_puts = {}
a = 0
for i, row in enumerate(puts.itertuples(), 0):

    if i == 0:
        start = False
        #break
    if (row.MSame == True):
        #reset target expiration, target strike 1st day of each month
        start=True
        newMonth = row.quote_date
        targetExpiration = row.quote_date + put_Expiration * Day()
        targetExpirationDifference = abs(row.expiration - targetExpiration)
        #if row.mid_underlying <20: put_moneyness= 1.00
        #if row.mid_underlying >20 and row.mid_underlying <30: put_moneyness= 1.00
        #if row.mid_underlying >30: put_moneyness= 0.80
        strikeTarget = row.mid_underlying * put_moneyness
        myStrikeDiff = abs(row.strike - strikeTarget)
        tempExpiration = row.expiration
        strikeLocation = (i)
    if start == True:

        if row.quote_date == newMonth and row.MSame == False:
            #iterate through the many different expirations and strikes for the first day of the new month
            #find the closest match to (a) targetExpiration and then (b) targetStrike

            if abs(targetExpiration -
                   row.expiration) < targetExpirationDifference:

                #error correction routine - when diff between target expiration and expiration continues to decline,
                #algo chooses the closer expirataion and then moves onto choose closest strike
                targetExpirationDifference = abs(targetExpiration -
                                                 row.expiration)
                myStrikeDiff = abs(row.strike - strikeTarget)
                tempExpiration = row.expiration
                strikeLocation = (i)

            if tempExpiration == row.expiration:
                if abs(strikeTarget - row.strike) <= myStrikeDiff:
                    myStrikeDiff = abs(strikeTarget - row.strike)
                    strikeLocation = (i)

            #closest to target expiration has been chosen. Using error correction algo now chooses
            #strike nearest to target strike

        if row.quote_date == newMonth and row.DSame == False:
            temp_puts[puts.quote_date[i]] = [
                i,
                puts.quote_date[i],
                puts.expiration[strikeLocation],
                puts.strike[strikeLocation],
                puts.trade_volume[strikeLocation],
                puts.mid_eod[strikeLocation],  #today's price                 
                newMonth,
                targetExpiration,
                targetExpirationDifference,
                puts.mid_underlying[strikeLocation],
                puts.futures[strikeLocation],
                strikeTarget,
                strikeLocation,
                myStrikeDiff
            ]

        if row.quote_date != newMonth and row.MSame == False:
            if row.expiration == puts.expiration[strikeLocation] and row.strike == puts.strike[strikeLocation]:
                temp_puts[puts.quote_date[i]] = [
                    i,
                    puts.quote_date[i],
                    puts.expiration[strikeLocation],
                    puts.strike[strikeLocation],
                    puts.trade_volume[i],
                    puts.mid_eod[i],  #today's price                
                    newMonth,
                    targetExpiration,
                    targetExpirationDifference,
                    puts.mid_underlying[i],
                    puts.futures[i],
                    strikeTarget,
                    strikeLocation,
                    myStrikeDiff
                ]

In [13]:
rolling_puts = pd.DataFrame(temp_puts).T.fillna(method='ffill')
rolling_puts.index.name = 'Date'
rolling_puts.columns = [
    'i', 'quote_date', 'expiration', 'strike', 'trade_volume', 'price',
    'newMonth', 'targetExpiration', 'ExpDiff', 'mid_underlying','futures',
    'strikeTarget', 'strikeLocation', 'StrikeDiff'
]
first_filter=rolling_puts.quote_date.isin(expiry_dates)
second_filter=rolling_puts.quote_date.isin(expiry_dates).shift(1)
rolling_puts['entry'] =(first_filter==True) & (second_filter==False)
rolling_puts['exit'] =rolling_puts.entry.shift(-1)
#rolling_puts['exit'] =(first_filter==True) & (second_filter==False)


In [14]:
rolling_puts.head()

i quote_date expiration  strike  trade_volume  price   newMonth  \
Date                                                                            
2006-04-19  714 2006-04-19 2006-05-17    22.5           0.0   9.90 2006-04-19   
2006-04-20  721 2006-04-20 2006-05-17    22.5           0.0  12.55 2006-04-19   
2006-04-21  729 2006-04-21 2006-05-17    22.5           0.0  12.35 2006-04-19   
2006-04-24  768 2006-04-24 2006-05-17    22.5          20.0  12.45 2006-04-19   
2006-04-25  807 2006-04-25 2006-05-17    22.5           0.0   9.90 2006-04-19   

           targetExpiration  ExpDiff  mid_underlying  futures  strikeTarget  \
Date                                                                          
2006-04-19       2006-11-05 172 days           11.32     22.5         11.32   
2006-04-20       2006-11-05 172 days           11.64     12.5         11.32   
2006-04-21       2006-11-05 172 days           11.59     12.5         11.32   
2006-04-24       2006-11-05 172 days           11.75     12.5         11.32   
2006-04-25       2006-11-05 172 days           11.76     12.5         11.32   

            strikeLocation  StrikeDiff  entry   exit  
Date                                                  
2006-04-19             714       11.18  False  False  
2006-04-20             714       11.18  False  False  
2006-04-21             714       11.18  False  False  
2006-04-24             714       11.18  False  False  
2006-04-25             714       11.18  False  False

In [15]:
#puts_file='../data/Options/vxxRolling_puts.csv'
puts_file='../data/Options/vix_rolling_puts.csv'
rolling_puts.to_csv(puts_file)

In [16]:
#initialise variables
#what length of option are you looking for in days?
call_Expiration = int(200)
#<1=ITM, 1=ATM, >1=OTM
call_moneyness = 2.00

In [17]:
#%%pixie_debugger
#initialise variables

temp_calls = {}
a = 0
for i, row in enumerate(calls.itertuples(), 0):

    if i == 0:
        start = False
        #break
    if (row.MSame == True):
        #reset target expiration, target strike 1st day of each month
        start=True
        newMonth = row.quote_date
        targetExpiration = row.quote_date + call_Expiration * Day()
        targetExpirationDifference = abs(row.expiration - targetExpiration)
        strikeTarget = row.mid_underlying * call_moneyness
        myStrikeDiff = abs(row.strike - strikeTarget)
        tempExpiration = row.expiration
        strikeLocation = (i)
    if start == True:

        if row.quote_date == newMonth and row.MSame == False:
            #iterate through the many different expirations and strikes for the first day of the new month
            #find the closest match to (a) targetExpiration and then (b) targetStrike

            if abs(targetExpiration -
                   row.expiration) < targetExpirationDifference:

                #error correction routine - when diff between target expiration and expiration continues to decline,
                #algo chooses the closer expirataion and then moves onto choose closest strike
                targetExpirationDifference = abs(targetExpiration -
                                                 row.expiration)
                myStrikeDiff = abs(row.strike - strikeTarget)
                tempExpiration = row.expiration
                strikeLocation = (i)

            if tempExpiration == row.expiration:
                if abs(strikeTarget - row.strike) <= myStrikeDiff:
                    myStrikeDiff = abs(strikeTarget - row.strike)
                    strikeLocation = (i)

#            #closest to target expiration has been chosen. Using error correction algo now chooses
#strike nearest to target strike

        if row.quote_date == newMonth and row.DSame == False:

            temp_calls[calls.quote_date[i]] = [
                i,
                calls.quote_date[i],
                calls.expiration[strikeLocation],
                calls.strike[strikeLocation],
                calls.trade_volume[strikeLocation],
                calls.mid_eod[strikeLocation],  #today's price                 
                newMonth,
                targetExpiration,
                targetExpirationDifference,
                calls.mid_underlying[strikeLocation],
                calls.futures[strikeLocation],
                strikeTarget,
                strikeLocation,
                myStrikeDiff
            ]

        if row.quote_date != newMonth and row.MSame == False:
            if row.expiration == calls.expiration[strikeLocation] and row.strike == calls.strike[strikeLocation]:
                temp_calls[calls.quote_date[i]] = [
                    i,
                    calls.quote_date[i],
                    calls.expiration[strikeLocation],
                    calls.strike[strikeLocation],
                    calls.trade_volume[i],
                    calls.mid_eod[i],  #today's price                
                    newMonth,
                    targetExpiration,
                    targetExpirationDifference,
                    calls.mid_underlying[i],
                    calls.futures[i],
                    strikeTarget,
                    strikeLocation,
                    myStrikeDiff
                ]

In [18]:
rolling_calls = pd.DataFrame(temp_calls).T.fillna(method='ffill')
rolling_calls.index.name = 'Date'
rolling_calls.columns = [
    'i', 'quote_date','expiration', 'strike','trade_volume','price', 'newMonth',
    'targetExpiration', 'ExpDiff', 'mid_underlying', 'futures','strikeTarget',
    'strikeLocation', 'StrikeDiff'
]
first_filter=rolling_calls.quote_date.isin(expiry_dates)
second_filter=rolling_calls.quote_date.isin(expiry_dates).shift(1)
rolling_calls['entry'] =(first_filter==True) & (second_filter==False)
rolling_calls['exit'] =rolling_calls.entry.shift(-1)


In [19]:
rolling_calls.head()

i quote_date expiration  strike  trade_volume  price   newMonth  \
Date                                                                            
2006-04-19  714 2006-04-19 2006-05-17    22.5           0.0  0.075 2006-04-19   
2006-04-20  721 2006-04-20 2006-05-17    22.5           0.0  0.075 2006-04-19   
2006-04-21  729 2006-04-21 2006-05-17    22.5           0.0  0.075 2006-04-19   
2006-04-24  768 2006-04-24 2006-05-17    22.5           0.0  0.075 2006-04-19   
2006-04-25  807 2006-04-25 2006-05-17    22.5           0.0  0.050 2006-04-19   

           targetExpiration  ExpDiff  mid_underlying  futures  strikeTarget  \
Date                                                                          
2006-04-19       2006-11-05 172 days           11.32     22.5         22.64   
2006-04-20       2006-11-05 172 days           11.64     12.5         22.64   
2006-04-21       2006-11-05 172 days           11.59     12.5         22.64   
2006-04-24       2006-11-05 172 days           11.75     12.5         22.64   
2006-04-25       2006-11-05 172 days           11.76     12.5         22.64   

            strikeLocation  StrikeDiff  entry   exit  
Date                                                  
2006-04-19             714        0.14  False  False  
2006-04-20             714        0.14  False  False  
2006-04-21             714        0.14  False  False  
2006-04-24             714        0.14  False  False  
2006-04-25             714        0.14  False  False

In [20]:
#calls_file='../data/Options/vxxRolling_calls.csv'
calls_file = '../data/Options/vix_rolling_calls.csv'
rolling_calls.to_csv(calls_file)

In [21]:
calls_file='../data/Options/vix_rolling_callsL.csv'
#rolling_calls.to_csv(calls_file)

In [22]:
calls_file='../data/Options/vix_rolling_callsS.csv'
#rolling_calls.to_csv(calls_file)